# Video Processing

In this tutorial, we'll first download some videos from TikTok, then transcribe the text from them, search the transcripts, and finally grab the frames (images) associated with the word we searched for.

# Scrape TikTok videos
## Install the modules for scraping TikTok

In [ ]:
!pip install pyktok
!pip install browser-cookie3
!pip install TikTokApi

## Scrape videos

`pyktok` is a python module for scraping TikTok. It saves metadata to spreadsheet (CSV) file, such as the username, date, etc. of the video. If you set the download parameter to `True` (like it is below), it will also download the video itself. (See the [pyktok website](https://github.com/dfreelon/pyktok#) for other functions like downloading up to 30 videos from a user page or hash tag, or downloading comments.)

First we will import the pyktok library, which we already installed above.

In [ ]:
import pyktok as pyk

Then create a variable `tiktok_videos` with a list of the videos we want to save. **You can replace these URLs with URLs of videos you want to save, but note two things**:
1. The videos must be accessible on TikTok without a login. (Let me know if you need to save login-protected videos.)
2. Each URL must have `'` around it, followed by a `,` (except the last item in the list.

In [ ]:
tiktok_videos = ['https://www.tiktok.com/@sarvinci/video/7136925515310501166',
                 'https://www.tiktok.com/@sarvinci/video/7108174973679881518',
                 'https://www.tiktok.com/@sarvinci/video/7300286760544652586']


Finally we use the `save_tiktok_multi_urls` function to save the videos and metadata.

In [ ]:
pyk.save_tiktok_multi_urls(tiktok_videos,
                           True, # Set to download videos (not just metadata).
                           'tiktok_data.csv', # Name of file results will be saved to
                           1)

If you open the files sidebar, you should be able to see the video files and the CSV file. Click the `...` button beside them if you'd like to download them to your computer.

## Get video filenames

For the next step, we'll need a variable (`converted_videos`) with the filenames of the videos we downloaded. Since the videos are named similarly to the URLs they came from, but with `_` instead of `/`, we can write a function to get the filenames from our earlier `tiktok_videos` variable.

In [ ]:
# This is a function to convert our previous list of TikTok URLs into a list of filenames of videos we downloaded.
# (The filenames have the username and the video id, which can be grabbed from the URL.)
def convert_tiktok_url(url):
    parts = url.split('/') # Each URL will be split into parts at the "/" character.
    username = parts[3] # The 4th part (counting 0) is the username.
    video_id = parts[5] # The 6th part is the video id.
    return f"{username}_video_{video_id}.mp4"

# This runs the function on each item in the list and saves the result in the variable converted_videos.
converted_videos = [convert_tiktok_url(url) for url in tiktok_videos]

# Show the result
print(converted_videos)

# Transcribe videos

## Install libraries

For the next steps, we will need the WhisperAi and ffmpeg libraries. Let's install them ...

In [ ]:
!pip install git+https://github.com/openai/whisper.git
!pip install ffmpeg-python

## Create a transcribe function

To transcribe an individual video, we can just do, e.g.,

`!whisper @sarvinci_video_7136925515310501166.mp4`

But we want to transcribe all of them, so we'll create a function for this.

In [ ]:
import subprocess

# This creates a function to run WhisperAI on a particular file. It is equivalent to doing whisper "filename", but by creating a function, we can do it on multiple videos in a row.
def run_whisper(filename):
    command = ['whisper', filename]
    subprocess.run(command)

## Run WhisperAI transcription

This next cell will take a while, because it downloads the WhisperAI model and then uses it to recognize the words in the videos and transcribe them.

In [ ]:
# Run whisper on each converted video filename
for video_file in converted_videos:
    run_whisper(video_file)

For each of the videos you downloaded, you should now have several files, such as `@sarvinci_video_7136925515310501166.json` and `@sarvinci_video_7136925515310501166.txt` which have the transcripts of the videos in them. Download one of them and take a look. They include the start and end time for every line of text.

## Get transcript JSON files

We're going to use the JSON files, so we need a list of these files. They have the same names as the MP4 files, so we can just change the end from `mp4` to `json`.

In [ ]:
transcript_files = [video_file.replace('.mp4','.json') for video_file in converted_videos]
print(transcript_files)

# Search the transcripts

Suppose we want to find specific words that occur in the video, and what segment they occur in. ChatGPT wrote this function for me. It creates the variable `results`, then goes segment by segment (line by line) through a transcript and adds the information for that segment to the `results` variable if it gets a hit on the search word.

In [ ]:
import json
import os

# Function to search for a word in the transcript
def search_word_in_transcript(word, transcript):
    results = []
    for segment in transcript['segments']:
        if word.lower() in segment['text'].lower():
            results.append({
                'filename': transcript['filename'],
                'start': segment['start'],
                'end': segment['end'],
                'text': segment['text']
            })
    return results

But we need something that can search for the same word across _all_ the transcripts in our `transcript_files` list. This function opens each of the .json files in the list and searches them for the `word` using the above function.

In [ ]:
# Main function to process all transcript files
def search_word_across_transcripts(word, transcript_files):
    all_results = []
    for transcript_file in transcript_files:
        with open(transcript_file, 'r', encoding='utf-8') as file:
            transcript = json.load(file)
            transcript['filename'] = transcript_file  # Add filename to transcript data
            results = search_word_in_transcript(word, transcript)
            all_results.extend(results)
    return all_results

Now we can do our search. Try changing the search word to e.g. "God" or "Baha'i".

In [ ]:
# Specify the word to search for
search_word = "faith"

# Search for the word across all transcripts
results = search_word_across_transcripts(search_word, transcript_files)

print(results)

Now we should save our results to a .json file, just in case we want to look at them later.

In [ ]:
# Save results to a file (optional)
output_file = 'search_results.json'
with open(output_file, 'w', encoding='utf-8') as file:
    json.dump(results, file, ensure_ascii=False, indent=4)

print(f"Results saved to {output_file}")

# Get the video frames for the search word

The function below uses `ffmpeg` to capture an image from a video at a particular time. Don't worry about the details, but it is the equivalent of running `ffmpeg` with some additional parameters in the command line. You don't need to change anything here.

In [ ]:
# Function to capture a still frame using ffmpeg
def capture_frame(video_file, capture_time, output_image):
    command = [
        'ffmpeg',
        '-i', video_file, # Which video file to capture from
        '-ss', str(capture_time), # What time in the video to capture
        '-vframes', '1',
        output_image # Where to save the image file
    ]
    subprocess.run(command, check=True)

Next, we'll loop through each of the results for our search word, and use the above function to grab an image.

In [ ]:
import subprocess

# Print and process the results
for result in results:
    filename = result['filename'].replace('.json','.mp4')
    print(f"Filename: {filename}, Start: {result['start']}, End: {result['end']}")
    print(f"Text: {result['text']}\n")

    # Calculate the halfway point
    capture_time = (result['start'] + result['end']) / 2

    # Set the output image filename
    base_filename = os.path.basename(filename).replace('.mp4', '')
    output_image = f"{base_filename}_{int(capture_time)}.png"

    # Capture the frame
    capture_frame(filename, capture_time, output_image)
    print(f"Captured frame at {capture_time} seconds: {output_image}")



You should now see some .png images in the Files sidebar. These will be the moments from the videos where your search word is mentioned.

# Download the results to your computer

Since Google Colab doesn't keep the files in the sidebar for more than a few minutes, you'll want to download them. You can do this by clicking on the `...` beside each file, but there are a lot of them. We can compress all the files ending in `.png` into a Zip file, then all the ones ending in `.json`, etc.

In [ ]:
!zip -r png.zip *.png # Compresses image (.png) files.
!zip -r json.zip *.json # Compresses .json files.
!zip -r mp4.zip *.mp4 # Compresses .mp4 files.

from google.colab import files
files.download("png.zip")
files.download("json.zip")
files.download("mp4.zip")

# You did it!

You can now search your selected TikTok videos for any word and get back not only the times this word occurs in the videos, but also the images the videos are showing at the time! If you want to use those images for further analysis now, such as recognizing objects or colors in them, you could.